In [1]:
import tweepy
from tweepy import OAuthHandler
import json
import datetime as dt
import time
import os
import sys

In [2]:
def load_api():
    ''' Function that loads the twitter API after authorizing the user. '''
# kshitij's keys
    consumer_key = "yyeI5zSWvvLVGSol7hu0tJ9gE"
    consumer_secret = "3N4fjsuLTCV4tIXEMICf587lM6mC7i8kcF4Ju1FSnx6VdKKLaW"
    access_token = "187109182-3vx120Tp28CEDfKZXB3JaZd5SV04DIZkhuIPEWfG"
    access_secret = "OXA5aGEXXqibb1FKl31EyVdLVVBqZnDrzS22oLy6KzCuh"
#     consumer_key = 'f9b5Ban5BdX8D1kIFyqFxq3Dz'
#     consumer_secret = 't1h5OfeidbJ1eDNfpPDlXKU6nPNI8RsSa5i00Q82HrS8dMvnaA'
#     access_token = '1083597947239944192-zgKRlZzEgvj5zaoBqhMfN5HpoXvRMc'
#     access_secret = 'gYnJt5Pd3CGDVHBgZ4FSK28XQt0OJMbeabhfY2JW7Esg3'
    auth = OAuthHandler(consumer_key, consumer_secret)
    auth.set_access_token(access_token, access_secret)
    # load the twitter API via tweepy
    return tweepy.API(auth)

In [3]:
def tweet_search(api, max_tweets, max_id, since_id):
    ''' Function that takes in a search string 'query', the maximum
        number of tweets 'max_tweets', and the minimum (i.e., starting)
        tweet id. It returns a list of tweepy.models.Status objects. '''

    searched_tweets = []
    while len(searched_tweets) < max_tweets:
        remaining_tweets = max_tweets - len(searched_tweets)
        try:
            new_tweets = api.search(q="#isis", count=remaining_tweets, since_id=str(since_id),max_id=str(max_id-1),tweet_mode = 'extended')
            print('found',len(new_tweets),'tweets')
            if not new_tweets:
                print('no tweets found')
                break
            searched_tweets.extend(new_tweets)
            max_id = new_tweets[-1].id
        except tweepy.TweepError:
            print('exception raised, waiting 15 minutes')
            print('(until:', dt.datetime.now()+dt.timedelta(minutes=15), ')')
            time.sleep(15*60)
            break # stop the loop
    return searched_tweets, max_id

In [4]:
def get_tweet_id(api, date='', days_ago=9, query='a'):
    ''' Function that gets the ID of a tweet. This ID can then be
        used as a 'starting point' from which to search. The query is
        required and has been set to a commonly used word by default.
        The variable 'days_ago' has been initialized to the maximum
        amount we are able to search back in time (9).'''

    if date:
        # return an ID from the start of the given day
        td = date + dt.timedelta(days=1)
        tweet_date = '{0}-{1:0>2}-{2:0>2}'.format(td.year, td.month, td.day)
        tweet = api.search(q=query, count=1, until=tweet_date)
    else:
        # return an ID from __ days ago
        td = dt.datetime.now() - dt.timedelta(days=days_ago)
        tweet_date = '{0}-{1:0>2}-{2:0>2}'.format(td.year, td.month, td.day)
        # get list of up to 10 tweets
        tweet = api.search(q=query, count=10, until=tweet_date)
        print('search limit (start/stop):',tweet[0].created_at)
        # return the id of the first tweet in the list
    return tweet[0].id

In [5]:
def write_tweets(tweets, filename):
    ''' Function that appends tweets to a file. '''

    with open(filename, 'a') as f:
        for tweet in tweets:
            json.dump(tweet._json, f)
            f.write('\n')

In [6]:
time_limit = 1.5                           # runtime limit in hours
max_tweets = 100                           # number of tweets per search (will be
                                               # iterated over) - maximum is 100
min_days_old, max_days_old = 6, 7          # search limits e.g., from 7 to 8
                                               # gives current weekday from last week,
                                               # min_days_old=0 will search from right now
Delhi = '28.626963,77.215396,50km'       # this geocode includes Delhi area
                                              
    

    # loop over search items,
    # creating a new file for each
    #for search_phrase in search_phrases:

     #   print('Search phrase =', search_phrase)

      #  ''' other variables '''
      #  name = search_phrase.split()[0]
      #  json_file_root = name + '/'  + name
       # os.makedirs(os.path.dirname(json_file_root), exist_ok=True)
read_IDs = False
        
        # open a file in which to store the tweets
if max_days_old - min_days_old == 1:
    d = dt.datetime.now() - dt.timedelta(days=min_days_old)
    day = '{0}-{1:0>2}-{2:0>2}'.format(d.year, d.month, d.day)
else:
    d1 = dt.datetime.now() - dt.timedelta(days=max_days_old-1)
    d2 = dt.datetime.now() - dt.timedelta(days=min_days_old)
    day = '{0}-{1:0>2}-{2:0>2}_to_{3}-{4:0>2}-{5:0>2}'.format(d1.year, d1.month, d1.day, d2.year, d2.month, d2.day)
json_file = 'Delhi' + '_' + day + '.json'
if os.path.isfile(json_file):
    print('Appending tweets to file named: ',json_file)
    read_IDs = True
        
        # authorize and load the twitter API
api = load_api()
        
        # set the 'starting point' ID for tweet collection
if read_IDs:
    # open the json file and get the latest tweet ID
    with open(json_file, 'r') as f:
        lines = f.readlines()
        max_id = json.loads(lines[-1])['id']
        print('Searching from the bottom ID in file')
else:
    # get the ID of a tweet that is min_days_old
    if min_days_old == 0:
        max_id = -1
    else:
        max_id = get_tweet_id(api, days_ago=(min_days_old-1))
    # set the smallest ID to search for
    since_id = get_tweet_id(api, days_ago=(max_days_old-1))
    print('max id (starting point) =', max_id)
    print('since id (ending point) =', since_id)
        


    ''' tweet gathering loop  '''
    start = dt.datetime.now()
    end = start + dt.timedelta(hours=time_limit)
    count, exitcount = 0, 0
    while dt.datetime.now() < end:
        count += 1
        print('count =',count)
        # collect tweets and update max_id
        tweets, max_id = tweet_search(api, max_tweets,max_id=max_id, since_id=since_id,
                                          )
            # write tweets to file in JSON format
        if tweets:
            write_tweets(tweets, json_file)
            exitcount = 0
        else:
            exitcount += 1
            if exitcount == 3:
                print('Maximum number of empty tweet strings reached - breaking')
                break

('search limit (start/stop):', datetime.datetime(2019, 2, 23, 23, 59, 59))
('search limit (start/stop):', datetime.datetime(2019, 2, 22, 23, 59, 59))
('max id (starting point) =', 1099458885834936321)
('since id (ending point) =', 1099096497973415936)
('count =', 1)
('found', 100, 'tweets')
('count =', 2)
('found', 100, 'tweets')
('count =', 3)
('found', 100, 'tweets')
('count =', 4)
('found', 100, 'tweets')
('count =', 5)
('found', 98, 'tweets')
('found', 2, 'tweets')
('count =', 6)
('found', 100, 'tweets')
('count =', 7)
('found', 100, 'tweets')
('count =', 8)
('found', 100, 'tweets')
('count =', 9)
('found', 100, 'tweets')
('count =', 10)
('found', 90, 'tweets')
('found', 10, 'tweets')
('count =', 11)
('found', 100, 'tweets')
('count =', 12)
('found', 100, 'tweets')
('count =', 13)
('found', 100, 'tweets')
('count =', 14)
('found', 100, 'tweets')
('count =', 15)
('found', 100, 'tweets')
('count =', 16)
('found', 100, 'tweets')
('count =', 17)
('found', 100, 'tweets')
('count =', 18)

In [7]:
with open(json_file, 'r') as f:
    lines = f.readlines()
    print(len(lines))

9286


In [8]:
lines

['{"contributors": null, "truncated": false, "is_quote_status": false, "in_reply_to_status_id": null, "id": 1099458844743233536, "favorite_count": 0, "full_text": "RT @BeholdIsrael: Al-Araby Al-Jadeed, pan-Arab media outlet headquartered in #London, reports on an #Israeli airstrike on #ISIS targets in\\u2026", "entities": {"symbols": [], "user_mentions": [{"id": 1225779630, "indices": [3, 16], "id_str": "1225779630", "screen_name": "BeholdIsrael", "name": "Amir Tsarfati"}], "hashtags": [{"indices": [77, 84], "text": "London"}, {"indices": [100, 108], "text": "Israeli"}, {"indices": [122, 127], "text": "ISIS"}], "urls": []}, "retweeted": false, "coordinates": null, "source": "<a href=\\"http://twitter.com/download/iphone\\" rel=\\"nofollow\\">Twitter for iPhone</a>", "in_reply_to_screen_name": null, "in_reply_to_user_id": null, "display_text_range": [0, 139], "retweet_count": 68, "id_str": "1099458844743233536", "favorited": false, "retweeted_status": {"contributors": null, "truncated":